In [1]:
from common import *

In [5]:
fnames = glob('../data/lingvo/raw/*')

In [6]:
dim = 300

In [9]:
import gc, io

def process(fnames, i):
    with io.open('../data/lingvo/%s.txt'%i, 'w', encoding='utf8') as fw:
        for fn in fnames:
            with io.open(fn, encoding='utf8') as fr:
                text = fr.read()
            sents = sent_tokenize(text)
            sents = [[w for w in s.split() if w not in stop_list and len(w)>1] for s in sents]
            sents = [s for s in sents if len(s)]
            s = json.dumps((basename(fn).split('.')[0], sents))            
            fw.write(s + u'\n')
    gc.collect()


In [10]:
parallelizer = Parallel(n_jobs=cpu_count-1)

tasks_iterator = ( delayed(process)(list_block, i) for 
                  i, list_block in enumerate(grouper(len(fnames)//500, fnames)) ) 
result = parallelizer( tasks_iterator )

In [13]:
import ujson

def iter_docs():
    with GzipFile('../data/lingvo/corpus_json.txt.gz', 'r') as fr:
        for line in fr:
            _id, sents = ujson.loads(line)
            yield _id, sents
    
def iter_sents():
    for _id, s in iter_docs():
        yield s
                
class Sentences(object):
    def __iter__(self):
        for sent in iter_sents():
            yield sent
            
class Documents(object):
    def __iter__(self):
        for _id, doc in iter_docs():
            unlisted = [w for s in doc for w in s]
            yield gensim.models.doc2vec.TaggedDocument(unlisted, [_id])

In [14]:
bigram = gensim.models.Phrases(iter_sents(), min_count=10, threshold=100)

2017-10-12 14:06:09,344 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-12 14:06:09,346 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words and 0 word types
2017-10-12 14:06:09,664 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 108194 words and 64779 word types
2017-10-12 14:06:09,980 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 215695 words and 117193 word types
2017-10-12 14:06:10,314 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 333525 words and 173755 word types
2017-10-12 14:06:10,676 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 456196 words and 229992 word types
2017-10-12 14:06:11,041 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 580554 words and 283552 word types
2017-10-12 14:06:11,385 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 695913 words and 337222 word types
2017-10-12 14:06:11,737 [MainThread  ] [INFO ]  PROGRESS: at sentenc

2017-10-12 14:06:30,416 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7143134 words and 2605065 word types
2017-10-12 14:06:30,737 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7252544 words and 2640090 word types
2017-10-12 14:06:31,085 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7369004 words and 2675118 word types
2017-10-12 14:06:31,398 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7474811 words and 2709165 word types
2017-10-12 14:06:31,723 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7585323 words and 2742729 word types
2017-10-12 14:06:32,078 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7706748 words and 2773507 word types
2017-10-12 14:06:32,537 [MainThread  ] [INFO ]  PROGRESS: at sentence #710000, processed 7817318 words and 2808664 word types
2017-10-12 14:06:32,856 [MainThread  ] [INFO ]  PROGRESS: at sentence #720000, processed 7923972 words and 2840609 wor

2017-10-12 14:06:51,702 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 14211202 words and 4609988 word types
2017-10-12 14:06:52,031 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 14321740 words and 4639420 word types
2017-10-12 14:06:52,359 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14427613 words and 4665375 word types
2017-10-12 14:06:52,720 [MainThread  ] [INFO ]  PROGRESS: at sentence #1330000, processed 14545425 words and 4698575 word types
2017-10-12 14:06:53,072 [MainThread  ] [INFO ]  PROGRESS: at sentence #1340000, processed 14665294 words and 4730750 word types
2017-10-12 14:06:53,414 [MainThread  ] [INFO ]  PROGRESS: at sentence #1350000, processed 14779144 words and 4760459 word types
2017-10-12 14:06:53,744 [MainThread  ] [INFO ]  PROGRESS: at sentence #1360000, processed 14888887 words and 4788175 word types
2017-10-12 14:06:54,064 [MainThread  ] [INFO ]  PROGRESS: at sentence #1370000, processed 14993756 words

2017-10-12 14:07:14,276 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 21474656 words and 6432126 word types
2017-10-12 14:07:14,593 [MainThread  ] [INFO ]  PROGRESS: at sentence #1960000, processed 21579555 words and 6456834 word types
2017-10-12 14:07:14,919 [MainThread  ] [INFO ]  PROGRESS: at sentence #1970000, processed 21687496 words and 6483948 word types
2017-10-12 14:07:15,263 [MainThread  ] [INFO ]  PROGRESS: at sentence #1980000, processed 21796228 words and 6509311 word types
2017-10-12 14:07:15,605 [MainThread  ] [INFO ]  PROGRESS: at sentence #1990000, processed 21908013 words and 6535414 word types
2017-10-12 14:07:15,949 [MainThread  ] [INFO ]  PROGRESS: at sentence #2000000, processed 22023635 words and 6561885 word types
2017-10-12 14:07:16,274 [MainThread  ] [INFO ]  PROGRESS: at sentence #2010000, processed 22131301 words and 6586573 word types
2017-10-12 14:07:16,665 [MainThread  ] [INFO ]  PROGRESS: at sentence #2020000, processed 22254321 words

2017-10-12 14:07:37,149 [MainThread  ] [INFO ]  PROGRESS: at sentence #2600000, processed 28604794 words and 8061287 word types
2017-10-12 14:07:37,501 [MainThread  ] [INFO ]  PROGRESS: at sentence #2610000, processed 28725042 words and 8084467 word types
2017-10-12 14:07:37,875 [MainThread  ] [INFO ]  PROGRESS: at sentence #2620000, processed 28848848 words and 8112240 word types
2017-10-12 14:07:38,214 [MainThread  ] [INFO ]  PROGRESS: at sentence #2630000, processed 28956498 words and 8136085 word types
2017-10-12 14:07:38,523 [MainThread  ] [INFO ]  PROGRESS: at sentence #2640000, processed 29057814 words and 8160006 word types
2017-10-12 14:07:38,857 [MainThread  ] [INFO ]  PROGRESS: at sentence #2650000, processed 29168285 words and 8184775 word types
2017-10-12 14:07:39,202 [MainThread  ] [INFO ]  PROGRESS: at sentence #2660000, processed 29278030 words and 8209029 word types
2017-10-12 14:07:39,545 [MainThread  ] [INFO ]  PROGRESS: at sentence #2670000, processed 29391056 words

...

2017-10-12 15:02:26,265 [MainThread  ] [INFO ]  PROGRESS: at sentence #87720000, processed 965172768 words and 31127602 word types
2017-10-12 15:02:26,630 [MainThread  ] [INFO ]  PROGRESS: at sentence #87730000, processed 965284243 words and 31140047 word types
2017-10-12 15:02:27,002 [MainThread  ] [INFO ]  PROGRESS: at sentence #87740000, processed 965399616 words and 31153345 word types
2017-10-12 15:02:27,329 [MainThread  ] [INFO ]  PROGRESS: at sentence #87750000, processed 965500057 words and 31166558 word types
2017-10-12 15:02:27,674 [MainThread  ] [INFO ]  PROGRESS: at sentence #87760000, processed 965609149 words and 31178782 word types
2017-10-12 15:02:28,026 [MainThread  ] [INFO ]  PROGRESS: at sentence #87770000, processed 965718900 words and 31191963 word types
2017-10-12 15:02:28,349 [MainThread  ] [INFO ]  PROGRESS: at sentence #87780000, processed 965820254 words and 31203487 word types
2017-10-12 15:02:28,704 [MainThread  ] [INFO ]  PROGRESS: at sentence #87790000, pr

2017-10-12 15:02:54,208 [MainThread  ] [INFO ]  PROGRESS: at sentence #88350000, processed 972055678 words and 31927683 word types
2017-10-12 15:02:54,571 [MainThread  ] [INFO ]  PROGRESS: at sentence #88360000, processed 972164177 words and 31939862 word types
2017-10-12 15:02:54,915 [MainThread  ] [INFO ]  PROGRESS: at sentence #88370000, processed 972273947 words and 31953669 word types
2017-10-12 15:02:55,282 [MainThread  ] [INFO ]  PROGRESS: at sentence #88380000, processed 972392290 words and 31966373 word types
2017-10-12 15:02:55,657 [MainThread  ] [INFO ]  PROGRESS: at sentence #88390000, processed 972507159 words and 31977827 word types
2017-10-12 15:02:56,056 [MainThread  ] [INFO ]  PROGRESS: at sentence #88400000, processed 972626983 words and 31992277 word types
2017-10-12 15:02:56,397 [MainThread  ] [INFO ]  PROGRESS: at sentence #88410000, processed 972732308 words and 32004944 word types
2017-10-12 15:02:56,741 [MainThread  ] [INFO ]  PROGRESS: at sentence #88420000, pr

2017-10-12 15:03:16,293 [MainThread  ] [INFO ]  PROGRESS: at sentence #88980000, processed 979044151 words and 32720280 word types
2017-10-12 15:03:16,655 [MainThread  ] [INFO ]  PROGRESS: at sentence #88990000, processed 979152172 words and 32733981 word types
2017-10-12 15:03:17,012 [MainThread  ] [INFO ]  PROGRESS: at sentence #89000000, processed 979263373 words and 32747050 word types
2017-10-12 15:03:17,375 [MainThread  ] [INFO ]  PROGRESS: at sentence #89010000, processed 979378317 words and 32757106 word types
2017-10-12 15:03:17,697 [MainThread  ] [INFO ]  PROGRESS: at sentence #89020000, processed 979481402 words and 32769022 word types
2017-10-12 15:03:18,039 [MainThread  ] [INFO ]  PROGRESS: at sentence #89030000, processed 979590456 words and 32781405 word types
2017-10-12 15:03:18,375 [MainThread  ] [INFO ]  PROGRESS: at sentence #89040000, processed 979695701 words and 32791701 word types
2017-10-12 15:03:18,724 [MainThread  ] [INFO ]  PROGRESS: at sentence #89050000, pr

2017-10-12 15:03:38,492 [MainThread  ] [INFO ]  PROGRESS: at sentence #89610000, processed 985985649 words and 33495976 word types
2017-10-12 15:03:38,869 [MainThread  ] [INFO ]  PROGRESS: at sentence #89620000, processed 986108850 words and 33510553 word types
2017-10-12 15:03:39,231 [MainThread  ] [INFO ]  PROGRESS: at sentence #89630000, processed 986224767 words and 33523509 word types
2017-10-12 15:03:39,582 [MainThread  ] [INFO ]  PROGRESS: at sentence #89640000, processed 986334956 words and 33537259 word types
2017-10-12 15:03:39,964 [MainThread  ] [INFO ]  PROGRESS: at sentence #89650000, processed 986452531 words and 33550935 word types
2017-10-12 15:03:40,324 [MainThread  ] [INFO ]  PROGRESS: at sentence #89660000, processed 986559816 words and 33564913 word types
2017-10-12 15:03:40,687 [MainThread  ] [INFO ]  PROGRESS: at sentence #89670000, processed 986672495 words and 33579922 word types
2017-10-12 15:03:41,048 [MainThread  ] [INFO ]  PROGRESS: at sentence #89680000, pr

2017-10-12 15:04:00,427 [MainThread  ] [INFO ]  PROGRESS: at sentence #90240000, processed 992831845 words and 34298503 word types
2017-10-12 15:04:00,763 [MainThread  ] [INFO ]  PROGRESS: at sentence #90250000, processed 992941017 words and 34311150 word types
2017-10-12 15:04:01,096 [MainThread  ] [INFO ]  PROGRESS: at sentence #90260000, processed 993047638 words and 34322865 word types
2017-10-12 15:04:01,441 [MainThread  ] [INFO ]  PROGRESS: at sentence #90270000, processed 993160321 words and 34334688 word types
2017-10-12 15:04:01,758 [MainThread  ] [INFO ]  PROGRESS: at sentence #90280000, processed 993263675 words and 34346470 word types
2017-10-12 15:04:02,111 [MainThread  ] [INFO ]  PROGRESS: at sentence #90290000, processed 993378620 words and 34357733 word types
2017-10-12 15:04:02,441 [MainThread  ] [INFO ]  PROGRESS: at sentence #90300000, processed 993482437 words and 34369401 word types
2017-10-12 15:04:02,779 [MainThread  ] [INFO ]  PROGRESS: at sentence #90310000, pr

In [15]:
bigram.save('../data/lingvo/bigram_10_100')

2017-10-12 15:04:19,251 [MainThread  ] [INFO ]  saving Phrases object under ../data/lingvo/bigram_10_100, separately None
2017-10-12 15:05:23,666 [MainThread  ] [INFO ]  saved ../data/lingvo/bigram_10_100


In [18]:
len(bigram.vocab)

29797470

In [16]:
len(bigram.vocab)

34974877

In [17]:
for phrase, score in bigram.export_phrases(islice(iter_sents(), 1000)):
    print('{0}   {1}'.format(phrase, score))

фашина биопозитивный   2099.45477013
гидротехнический мелиоративный   137.855047255
природоохранный берегоукрепительный   1073.03550719
русло река   234.025276635
многолетний трава   125.153362902
гидротехнический мелиоративный   137.855047255
природоохранный берегоукрепительный   1073.03550719
русло река   234.025276635
многолетний трава   125.153362902
фашина биопозитивный   2099.45477013
многолетний трава   125.153362902
фашина биопозитивный   2099.45477013
фашина биопозитивный   2099.45477013
рассредоточиваться гаситься   233.772095635
фашина биопозитивный   2099.45477013
предгорный равнинный   772.712002209
природоохранный законодательство   289.30111099
гидротехнический сооружение   138.356256334
сельхозиздатый 1962   253.342003854
многолетний трава   125.153362902
гидротехнический сооружение   138.356256334
континентальный шельф   4487.20457305
гидротехнический сооружение   138.356256334
континентальный шельф   4487.20457305
винтокрылый ветроприемник   177.351992333
винтокрылый 

In [31]:
bigram = gensim.models.phrases.Phrases.load('../data/lingvo/bigram_5_100')

2017-10-09 21:37:51,276 [MainThread  ] [INFO ]  loading Phrases object from ../data/lingvo/bigram_5_100
2017-10-09 21:38:17,725 [MainThread  ] [INFO ]  loaded ../data/lingvo/bigram_5_100


In [ ]:
bigram_ph = gensim.models.phrases.Phraser(bigram)

2017-10-12 15:05:53,688 [MainThread  ] [INFO ]  source_vocab length 34974877
2017-10-12 15:06:59,192 [MainThread  ] [INFO ]  Phraser added 50000 phrasegrams
2017-10-12 15:08:13,107 [MainThread  ] [INFO ]  Phraser added 100000 phrasegrams
2017-10-12 15:09:28,837 [MainThread  ] [INFO ]  Phraser added 150000 phrasegrams
2017-10-12 15:10:46,072 [MainThread  ] [INFO ]  Phraser added 200000 phrasegrams
2017-10-12 15:12:06,276 [MainThread  ] [INFO ]  Phraser added 250000 phrasegrams
2017-10-12 15:13:27,494 [MainThread  ] [INFO ]  Phraser added 300000 phrasegrams
2017-10-12 15:14:48,848 [MainThread  ] [INFO ]  Phraser added 350000 phrasegrams
2017-10-12 15:15:27,423 [MainThread  ] [INFO ]  Phraser built with 373565 373565 phrasegrams


In [ ]:
bigram_ph.save('../data/lingvo/bigram_ph_10_100')

2017-10-12 15:15:27,432 [MainThread  ] [INFO ]  saving Phraser object under ../data/lingvo/bigram_ph_10_100, separately None
2017-10-12 15:15:27,996 [MainThread  ] [INFO ]  saved ../data/lingvo/bigram_ph_10_100


In [19]:
bigram_ph = gensim.models.phrases.Phraser.load('../data/lingvo/bigram_ph_10_100')

2017-10-12 18:17:33,307 [MainThread  ] [INFO ]  loading Phraser object from ../data/lingvo/bigram_ph_10_100
2017-10-12 18:17:33,799 [MainThread  ] [INFO ]  loaded ../data/lingvo/bigram_ph_10_100


In [ ]:
trigram = gensim.models.Phrases(bigram_ph[iter_sents()], min_count=5, threshold=10)

2017-10-12 15:15:28,004 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-12 15:15:28,005 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words and 0 word types
2017-10-12 15:15:28,943 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 105877 words and 64295 word types
2017-10-12 15:15:29,840 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 209956 words and 116659 word types
2017-10-12 15:15:30,808 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 323012 words and 173227 word types
2017-10-12 15:15:31,842 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 441487 words and 229324 word types
2017-10-12 15:15:32,883 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 562465 words and 282867 word types
2017-10-12 15:15:33,857 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 675972 words and 336481 word types
2017-10-12 15:15:34,866 [MainThread  ] [INFO ]  PROGRESS: at sentenc

2017-10-12 15:16:30,676 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 6966790 words and 2621992 word types
2017-10-12 15:16:31,631 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7072425 words and 2657464 word types
2017-10-12 15:16:32,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7185662 words and 2692864 word types
2017-10-12 15:16:33,625 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7289838 words and 2727187 word types
2017-10-12 15:16:34,652 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7397852 words and 2761145 word types
2017-10-12 15:16:35,691 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7514793 words and 2792319 word types
2017-10-12 15:16:36,876 [MainThread  ] [INFO ]  PROGRESS: at sentence #710000, processed 7623261 words and 2827883 word types
2017-10-12 15:16:37,801 [MainThread  ] [INFO ]  PROGRESS: at sentence #720000, processed 7727413 words and 2860276 wor

2017-10-12 15:17:32,060 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 13867651 words and 4657753 word types
2017-10-12 15:17:33,014 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 13975898 words and 4687588 word types
2017-10-12 15:17:33,903 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14079968 words and 4713971 word types
2017-10-12 15:17:34,893 [MainThread  ] [INFO ]  PROGRESS: at sentence #1330000, processed 14193463 words and 4747827 word types
2017-10-12 15:17:35,927 [MainThread  ] [INFO ]  PROGRESS: at sentence #1340000, processed 14309859 words and 4780489 word types
2017-10-12 15:17:36,889 [MainThread  ] [INFO ]  PROGRESS: at sentence #1350000, processed 14420998 words and 4810699 word types
2017-10-12 15:17:37,830 [MainThread  ] [INFO ]  PROGRESS: at sentence #1360000, processed 14528426 words and 4838877 word types
2017-10-12 15:17:38,719 [MainThread  ] [INFO ]  PROGRESS: at sentence #1370000, processed 14630970 words

2017-10-12 15:18:34,624 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 20947299 words and 6514826 word types
2017-10-12 15:18:35,517 [MainThread  ] [INFO ]  PROGRESS: at sentence #1960000, processed 21050357 words and 6539925 word types
2017-10-12 15:18:36,427 [MainThread  ] [INFO ]  PROGRESS: at sentence #1970000, processed 21155899 words and 6567528 word types
2017-10-12 15:18:44,813 [MainThread  ] [INFO ]  PROGRESS: at sentence #1980000, processed 21262278 words and 6593464 word types
2017-10-12 15:18:45,804 [MainThread  ] [INFO ]  PROGRESS: at sentence #1990000, processed 21371353 words and 6620062 word types
2017-10-12 15:18:46,818 [MainThread  ] [INFO ]  PROGRESS: at sentence #2000000, processed 21484436 words and 6646944 word types
2017-10-12 15:18:47,764 [MainThread  ] [INFO ]  PROGRESS: at sentence #2010000, processed 21590620 words and 6671993 word types
2017-10-12 15:18:48,803 [MainThread  ] [INFO ]  PROGRESS: at sentence #2020000, processed 21710269 words

2017-10-12 15:19:44,179 [MainThread  ] [INFO ]  PROGRESS: at sentence #2600000, processed 27912931 words and 8178793 word types
2017-10-12 15:19:45,223 [MainThread  ] [INFO ]  PROGRESS: at sentence #2610000, processed 28029025 words and 8202555 word types
2017-10-12 15:19:46,280 [MainThread  ] [INFO ]  PROGRESS: at sentence #2620000, processed 28148702 words and 8231372 word types
2017-10-12 15:19:47,223 [MainThread  ] [INFO ]  PROGRESS: at sentence #2630000, processed 28254410 words and 8255691 word types
2017-10-12 15:19:48,097 [MainThread  ] [INFO ]  PROGRESS: at sentence #2640000, processed 28353436 words and 8280101 word types
2017-10-12 15:19:49,096 [MainThread  ] [INFO ]  PROGRESS: at sentence #2650000, processed 28461967 words and 8305344 word types
2017-10-12 15:19:50,078 [MainThread  ] [INFO ]  PROGRESS: at sentence #2660000, processed 28569696 words and 8329954 word types
2017-10-12 15:19:51,074 [MainThread  ] [INFO ]  PROGRESS: at sentence #2670000, processed 28680655 words

...

2017-10-12 16:23:50,912 [MainThread  ] [INFO ]  PROGRESS: at sentence #40490000, processed 434386980 words and 19851901 word types
2017-10-12 16:23:51,886 [MainThread  ] [INFO ]  PROGRESS: at sentence #40500000, processed 434494569 words and 19868415 word types
2017-10-12 16:23:52,899 [MainThread  ] [INFO ]  PROGRESS: at sentence #40510000, processed 434610335 words and 19882953 word types
2017-10-12 16:23:53,853 [MainThread  ] [INFO ]  PROGRESS: at sentence #40520000, processed 434716256 words and 19898643 word types
2017-10-12 16:23:54,809 [MainThread  ] [INFO ]  PROGRESS: at sentence #40530000, processed 434824417 words and 19913897 word types
2017-10-12 16:23:55,774 [MainThread  ] [INFO ]  PROGRESS: at sentence #40540000, processed 434932712 words and 19928833 word types
2017-10-12 16:23:56,756 [MainThread  ] [INFO ]  PROGRESS: at sentence #40550000, processed 435042018 words and 19944076 word types
2017-10-12 16:23:57,707 [MainThread  ] [INFO ]  PROGRESS: at sentence #40560000, pr

2017-10-12 16:24:51,634 [MainThread  ] [INFO ]  PROGRESS: at sentence #41120000, processed 441073896 words and 20793472 word types
2017-10-12 16:24:52,600 [MainThread  ] [INFO ]  PROGRESS: at sentence #41130000, processed 441180209 words and 20809608 word types
2017-10-12 16:24:53,562 [MainThread  ] [INFO ]  PROGRESS: at sentence #41140000, processed 441282954 words and 20823316 word types
2017-10-12 16:24:54,573 [MainThread  ] [INFO ]  PROGRESS: at sentence #41150000, processed 441395106 words and 20841503 word types
2017-10-12 16:24:55,646 [MainThread  ] [INFO ]  PROGRESS: at sentence #41160000, processed 441512231 words and 20858409 word types
2017-10-12 16:24:56,701 [MainThread  ] [INFO ]  PROGRESS: at sentence #41170000, processed 441630317 words and 20874113 word types
2017-10-12 16:24:57,647 [MainThread  ] [INFO ]  PROGRESS: at sentence #41180000, processed 441730784 words and 20892914 word types
2017-10-12 16:24:58,569 [MainThread  ] [INFO ]  PROGRESS: at sentence #41190000, pr

2017-10-12 16:25:53,045 [MainThread  ] [INFO ]  PROGRESS: at sentence #41750000, processed 447825655 words and 21764828 word types
2017-10-12 16:25:54,051 [MainThread  ] [INFO ]  PROGRESS: at sentence #41760000, processed 447933751 words and 21781150 word types
2017-10-12 16:25:55,018 [MainThread  ] [INFO ]  PROGRESS: at sentence #41770000, processed 448039164 words and 21796327 word types
2017-10-12 16:25:55,963 [MainThread  ] [INFO ]  PROGRESS: at sentence #41780000, processed 448143314 words and 21811432 word types
2017-10-12 16:25:56,915 [MainThread  ] [INFO ]  PROGRESS: at sentence #41790000, processed 448247077 words and 21827962 word types
2017-10-12 16:25:57,957 [MainThread  ] [INFO ]  PROGRESS: at sentence #41800000, processed 448362174 words and 21843315 word types
2017-10-12 16:25:58,940 [MainThread  ] [INFO ]  PROGRESS: at sentence #41810000, processed 448471909 words and 21859160 word types
2017-10-12 16:25:59,911 [MainThread  ] [INFO ]  PROGRESS: at sentence #41820000, pr

2017-10-12 16:26:54,747 [MainThread  ] [INFO ]  PROGRESS: at sentence #42380000, processed 454607460 words and 22736045 word types
2017-10-12 16:26:55,833 [MainThread  ] [INFO ]  PROGRESS: at sentence #42390000, processed 454730299 words and 22753002 word types
2017-10-12 16:26:56,802 [MainThread  ] [INFO ]  PROGRESS: at sentence #42400000, processed 454839922 words and 22767665 word types
2017-10-12 16:26:57,802 [MainThread  ] [INFO ]  PROGRESS: at sentence #42410000, processed 454952005 words and 22780181 word types
2017-10-12 16:26:58,765 [MainThread  ] [INFO ]  PROGRESS: at sentence #42420000, processed 455060163 words and 22794207 word types
2017-10-12 16:26:59,708 [MainThread  ] [INFO ]  PROGRESS: at sentence #42430000, processed 455166463 words and 22810417 word types
2017-10-12 16:27:00,615 [MainThread  ] [INFO ]  PROGRESS: at sentence #42440000, processed 455267832 words and 22825985 word types
2017-10-12 16:27:01,634 [MainThread  ] [INFO ]  PROGRESS: at sentence #42450000, pr

2017-10-12 16:27:55,865 [MainThread  ] [INFO ]  PROGRESS: at sentence #43010000, processed 461406755 words and 23666377 word types
2017-10-12 16:27:56,853 [MainThread  ] [INFO ]  PROGRESS: at sentence #43020000, processed 461514982 words and 23681055 word types
2017-10-12 16:27:57,807 [MainThread  ] [INFO ]  PROGRESS: at sentence #43030000, processed 461619762 words and 23694927 word types
2017-10-12 16:27:58,826 [MainThread  ] [INFO ]  PROGRESS: at sentence #43040000, processed 461730277 words and 23708128 word types
2017-10-12 16:27:59,860 [MainThread  ] [INFO ]  PROGRESS: at sentence #43050000, processed 461845331 words and 23722296 word types
2017-10-12 16:28:00,896 [MainThread  ] [INFO ]  PROGRESS: at sentence #43060000, processed 461961864 words and 23740086 word types
2017-10-12 16:28:01,845 [MainThread  ] [INFO ]  PROGRESS: at sentence #43070000, processed 462067434 words and 23755086 word types
2017-10-12 16:28:02,815 [MainThread  ] [INFO ]  PROGRESS: at sentence #43080000, pr

In [ ]:
trigram.save('../data/lingvo/trigram')

In [16]:
trigram = gensim.models.phrases.Phrases.load(join(DATA_FOLDER, '../data/lingvo/trigram'))

2017-10-12 18:16:39,324 [MainThread  ] [INFO ]  loading Phrases object from ../data/../data/lingvo/trigram
2017-10-12 18:17:05,864 [MainThread  ] [INFO ]  loaded ../data/../data/lingvo/trigram


In [9]:
for s in islice(trigram[bigram_ph[iter_sents()]], 100):
    for w in s:
        if len(w.split('_')) > 2:
            print(w)

/usr/local/lib/python2.7/dist-packages/gensim/models/phrases.py:316: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


тяжелый_фашина_биопозитивный_конструкция
гидротехнический_мелиоративный_строительство
тяжелый_фашина_грунтовой
заполнить_плодородный_грунт
семя_многолетний_трава
кустарник_развитый_корневой
гидротехнический_мелиоративный_строительство
тяжелый_фашина_грунтовой
заполнить_плодородный_грунт
семя_многолетний_трава
кустарник_развитый_корневой
мешок_плодородный_грунт
тяжелый_фашина_биопозитивный_конструкция
семя_многолетний_трава
тяжелый_фашина_биопозитивный_конструкция
мешок_плодородный_грунт
отрезать_заготавливать_габионный
тяжелый_фашина_биопозитивный_конструкция
рассредоточиваться_гаситься_гибкость
размыв_русло_низ
максимально_размыв_русло
плодородный_грунт_влажный
семя_трава_кустарник
корневой_трава_кустарник
откос_берег_дамба
сильный_укрепляться_сливаться
естественный_ландшафт_прибрежный
малек_рыба_питаться
личинка_насекомое_зеленый
включаться_экосистема_река
тяжелый_фашина_биопозитивный_конструкция
требование_природоохранный_законодательство
тяжелый_фашина_грунтовой
заполнить_плодородн

In [22]:
trigram_ph = gensim.models.phrases.Phraser(trigram)
trigram_ph.save('../data/lingvo/trigram_ph')

2017-10-12 17:50:59,320 [MainThread  ] [INFO ]  source_vocab length 39774335
2017-10-12 17:51:13,161 [MainThread  ] [INFO ]  Phraser added 50000 phrasegrams
2017-10-12 17:51:26,238 [MainThread  ] [INFO ]  Phraser added 100000 phrasegrams
2017-10-12 17:51:39,349 [MainThread  ] [INFO ]  Phraser added 150000 phrasegrams
2017-10-12 17:51:52,250 [MainThread  ] [INFO ]  Phraser added 200000 phrasegrams
2017-10-12 17:52:05,536 [MainThread  ] [INFO ]  Phraser added 250000 phrasegrams
2017-10-12 17:52:18,591 [MainThread  ] [INFO ]  Phraser added 300000 phrasegrams
2017-10-12 17:52:31,359 [MainThread  ] [INFO ]  Phraser added 350000 phrasegrams
2017-10-12 17:52:44,509 [MainThread  ] [INFO ]  Phraser added 400000 phrasegrams
2017-10-12 17:52:58,426 [MainThread  ] [INFO ]  Phraser added 450000 phrasegrams
2017-10-12 17:53:12,175 [MainThread  ] [INFO ]  Phraser added 500000 phrasegrams
2017-10-12 17:53:25,206 [MainThread  ] [INFO ]  Phraser added 550000 phrasegrams
2017-10-12 17:53:38,365 [MainThre

In [ ]:
model = Word2Vec(Sentences(), size=dim, sg=1, min_count=10, window=10, workers=8)

2017-10-13 12:05:54,498 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-13 12:05:54,513 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2017-10-13 12:05:54,675 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 108194 words, keeping 11923 word types
2017-10-13 12:05:54,856 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 215695 words, keeping 18597 word types
2017-10-13 12:05:54,990 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 333525 words, keeping 25805 word types
2017-10-13 12:05:55,139 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 456196 words, keeping 32259 word types
2017-10-13 12:05:55,294 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 580554 words, keeping 37391 word types
2017-10-13 12:05:55,436 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 695913 words, keeping 41846 word types
2017-10-13 12:05:55,582 [MainThread  ]

2017-10-13 12:06:03,189 [MainThread  ] [INFO ]  PROGRESS: at sentence #630000, processed 6912698 words, keeping 212405 word types
2017-10-13 12:06:03,334 [MainThread  ] [INFO ]  PROGRESS: at sentence #640000, processed 7029422 words, keeping 214492 word types
2017-10-13 12:06:03,479 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 7143134 words, keeping 216730 word types
2017-10-13 12:06:03,616 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 7252544 words, keeping 219287 word types
2017-10-13 12:06:03,764 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 7369004 words, keeping 221799 word types
2017-10-13 12:06:03,894 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 7474811 words, keeping 223765 word types
2017-10-13 12:06:04,030 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 7585323 words, keeping 226257 word types
2017-10-13 12:06:04,174 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 7

2017-10-13 12:06:11,826 [MainThread  ] [INFO ]  PROGRESS: at sentence #1260000, processed 13775627 words, keeping 347112 word types
2017-10-13 12:06:11,961 [MainThread  ] [INFO ]  PROGRESS: at sentence #1270000, processed 13881680 words, keeping 349401 word types
2017-10-13 12:06:12,138 [MainThread  ] [INFO ]  PROGRESS: at sentence #1280000, processed 13998165 words, keeping 352595 word types
2017-10-13 12:06:12,261 [MainThread  ] [INFO ]  PROGRESS: at sentence #1290000, processed 14097940 words, keeping 354205 word types
2017-10-13 12:06:12,403 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 14211202 words, keeping 355867 word types
2017-10-13 12:06:12,546 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 14321740 words, keeping 357628 word types
2017-10-13 12:06:12,685 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 14427613 words, keeping 358908 word types
2017-10-13 12:06:12,833 [MainThread  ] [INFO ]  PROGRESS: at sentence #13300

2017-10-13 12:06:21,036 [MainThread  ] [INFO ]  PROGRESS: at sentence #1890000, processed 20776871 words, keeping 468625 word types
2017-10-13 12:06:21,159 [MainThread  ] [INFO ]  PROGRESS: at sentence #1900000, processed 20888023 words, keeping 470846 word types
2017-10-13 12:06:21,293 [MainThread  ] [INFO ]  PROGRESS: at sentence #1910000, processed 20994697 words, keeping 472655 word types
2017-10-13 12:06:21,465 [MainThread  ] [INFO ]  PROGRESS: at sentence #1920000, processed 21129632 words, keeping 483234 word types
2017-10-13 12:06:21,609 [MainThread  ] [INFO ]  PROGRESS: at sentence #1930000, processed 21241099 words, keeping 484939 word types
2017-10-13 12:06:21,761 [MainThread  ] [INFO ]  PROGRESS: at sentence #1940000, processed 21360694 words, keeping 486726 word types
2017-10-13 12:06:21,915 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 21474656 words, keeping 488201 word types
2017-10-13 12:06:22,054 [MainThread  ] [INFO ]  PROGRESS: at sentence #19600

2017-10-13 12:06:35,568 [MainThread  ] [INFO ]  PROGRESS: at sentence #2520000, processed 27727349 words, keeping 580795 word types
2017-10-13 12:06:35,707 [MainThread  ] [INFO ]  PROGRESS: at sentence #2530000, processed 27833182 words, keeping 582434 word types
2017-10-13 12:06:35,848 [MainThread  ] [INFO ]  PROGRESS: at sentence #2540000, processed 27941401 words, keeping 584349 word types
2017-10-13 12:06:35,987 [MainThread  ] [INFO ]  PROGRESS: at sentence #2550000, processed 28051040 words, keeping 586012 word types
2017-10-13 12:06:36,134 [MainThread  ] [INFO ]  PROGRESS: at sentence #2560000, processed 28166192 words, keeping 587900 word types
2017-10-13 12:06:36,292 [MainThread  ] [INFO ]  PROGRESS: at sentence #2570000, processed 28282356 words, keeping 589201 word types
2017-10-13 12:06:36,440 [MainThread  ] [INFO ]  PROGRESS: at sentence #2580000, processed 28395935 words, keeping 590573 word types
2017-10-13 12:06:36,581 [MainThread  ] [INFO ]  PROGRESS: at sentence #25900

...

2017-10-13 17:44:50,706 [MainThread  ] [INFO ]  PROGRESS: at 54.43% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:51,744 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:52,777 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:53,803 [MainThread  ] [INFO ]  PROGRESS: at 54.44% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:54,813 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153086 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:55,810 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153086 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:56,826 [MainThread  ] [INFO ]  PROGRESS: at 54.45% examples, 153087 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:44:58,185 [MainThread  ] [INFO ]  PROGRESS: at 54.46% examples, 153083 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:44:59,194 [MainThread  ] [INFO ]  

2017-10-13 17:46:03,322 [MainThread  ] [INFO ]  PROGRESS: at 54.66% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:04,337 [MainThread  ] [INFO ]  PROGRESS: at 54.66% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:05,376 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:06,398 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:07,412 [MainThread  ] [INFO ]  PROGRESS: at 54.67% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:08,463 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:09,471 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153085 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:10,647 [MainThread  ] [INFO ]  PROGRESS: at 54.68% examples, 153084 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:46:11,657 [MainThread  ] [INFO ]  

2017-10-13 17:47:15,934 [MainThread  ] [INFO ]  PROGRESS: at 54.88% examples, 153079 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:16,971 [MainThread  ] [INFO ]  PROGRESS: at 54.89% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:18,135 [MainThread  ] [INFO ]  PROGRESS: at 54.89% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:19,199 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:20,203 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:21,303 [MainThread  ] [INFO ]  PROGRESS: at 54.90% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:22,319 [MainThread  ] [INFO ]  PROGRESS: at 54.91% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:47:23,362 [MainThread  ] [INFO ]  PROGRESS: at 54.91% examples, 153082 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:47:24,407 [MainThread  ] [INFO ]  

2017-10-13 17:48:30,062 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:31,133 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:32,139 [MainThread  ] [INFO ]  PROGRESS: at 55.12% examples, 153082 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:33,141 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153082 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:34,168 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:35,315 [MainThread  ] [INFO ]  PROGRESS: at 55.13% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:48:36,310 [MainThread  ] [INFO ]  PROGRESS: at 55.14% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:37,471 [MainThread  ] [INFO ]  PROGRESS: at 55.14% examples, 153081 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:48:38,524 [MainThread  ] [INFO ]  

2017-10-13 17:49:43,067 [MainThread  ] [INFO ]  PROGRESS: at 55.34% examples, 153079 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:44,199 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153079 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:49:45,225 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:46,251 [MainThread  ] [INFO ]  PROGRESS: at 55.35% examples, 153080 words/s, in_qsize 16, out_qsize 0
2017-10-13 17:49:47,305 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:48,308 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:49,322 [MainThread  ] [INFO ]  PROGRESS: at 55.36% examples, 153080 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:50,381 [MainThread  ] [INFO ]  PROGRESS: at 55.37% examples, 153081 words/s, in_qsize 15, out_qsize 0
2017-10-13 17:49:51,420 [MainThread  ] [INFO ]  

In [ ]:
model.save('../data/lingvo/w2v_300_sg_10_w10')

In [ ]:
model = Word2Vec(trigram[bigram_ph[Sentences()]], size=dim, sg=1, min_count=5, window=10, workers=cpu_count)

2017-10-12 18:18:09,698 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-12 18:18:09,700 [MainThread  ] [INFO ]  PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2017-10-12 18:18:11,187 [MainThread  ] [INFO ]  PROGRESS: at sentence #10000, processed 97302 words, keeping 12949 word types
2017-10-12 18:18:12,623 [MainThread  ] [INFO ]  PROGRESS: at sentence #20000, processed 192868 words, keeping 21042 word types
2017-10-12 18:18:14,181 [MainThread  ] [INFO ]  PROGRESS: at sentence #30000, processed 295614 words, keeping 30091 word types
2017-10-12 18:18:15,789 [MainThread  ] [INFO ]  PROGRESS: at sentence #40000, processed 402080 words, keeping 38362 word types
2017-10-12 18:18:17,405 [MainThread  ] [INFO ]  PROGRESS: at sentence #50000, processed 512727 words, keeping 45220 word types
2017-10-12 18:18:18,947 [MainThread  ] [INFO ]  PROGRESS: at sentence #60000, processed 618796 words, keeping 51389 word types
2017-10-12 18:18:20,534 [MainThread  ] 

2017-10-12 18:19:44,356 [MainThread  ] [INFO ]  PROGRESS: at sentence #630000, processed 6168199 words, keeping 302059 word types
2017-10-12 18:19:45,904 [MainThread  ] [INFO ]  PROGRESS: at sentence #640000, processed 6270026 words, keeping 305282 word types
2017-10-12 18:19:47,437 [MainThread  ] [INFO ]  PROGRESS: at sentence #650000, processed 6371833 words, keeping 309010 word types
2017-10-12 18:19:48,903 [MainThread  ] [INFO ]  PROGRESS: at sentence #660000, processed 6467165 words, keeping 312949 word types
2017-10-12 18:19:50,472 [MainThread  ] [INFO ]  PROGRESS: at sentence #670000, processed 6570342 words, keeping 316818 word types
2017-10-12 18:19:51,945 [MainThread  ] [INFO ]  PROGRESS: at sentence #680000, processed 6667243 words, keeping 319884 word types
2017-10-12 18:19:53,447 [MainThread  ] [INFO ]  PROGRESS: at sentence #690000, processed 6765840 words, keeping 323599 word types
2017-10-12 18:19:55,040 [MainThread  ] [INFO ]  PROGRESS: at sentence #700000, processed 6

2017-10-12 18:21:17,145 [MainThread  ] [INFO ]  PROGRESS: at sentence #1260000, processed 12294824 words, keeping 510980 word types
2017-10-12 18:21:18,581 [MainThread  ] [INFO ]  PROGRESS: at sentence #1270000, processed 12390780 words, keeping 514206 word types
2017-10-12 18:21:20,118 [MainThread  ] [INFO ]  PROGRESS: at sentence #1280000, processed 12493201 words, keeping 518665 word types
2017-10-12 18:21:21,473 [MainThread  ] [INFO ]  PROGRESS: at sentence #1290000, processed 12580941 words, keeping 521152 word types
2017-10-12 18:21:22,958 [MainThread  ] [INFO ]  PROGRESS: at sentence #1300000, processed 12680035 words, keeping 523673 word types
2017-10-12 18:21:24,437 [MainThread  ] [INFO ]  PROGRESS: at sentence #1310000, processed 12780221 words, keeping 526398 word types
2017-10-12 18:21:25,918 [MainThread  ] [INFO ]  PROGRESS: at sentence #1320000, processed 12877042 words, keeping 528477 word types
2017-10-12 18:21:27,461 [MainThread  ] [INFO ]  PROGRESS: at sentence #13300

2017-10-12 18:22:52,007 [MainThread  ] [INFO ]  PROGRESS: at sentence #1890000, processed 18527019 words, keeping 694693 word types
2017-10-12 18:22:53,492 [MainThread  ] [INFO ]  PROGRESS: at sentence #1900000, processed 18625125 words, keeping 697810 word types
2017-10-12 18:22:55,070 [MainThread  ] [INFO ]  PROGRESS: at sentence #1910000, processed 18720793 words, keeping 700642 word types
2017-10-12 18:22:56,788 [MainThread  ] [INFO ]  PROGRESS: at sentence #1920000, processed 18834616 words, keeping 712295 word types
2017-10-12 18:22:58,324 [MainThread  ] [INFO ]  PROGRESS: at sentence #1930000, processed 18935439 words, keeping 714975 word types
2017-10-12 18:22:59,967 [MainThread  ] [INFO ]  PROGRESS: at sentence #1940000, processed 19039850 words, keeping 717888 word types
2017-10-12 18:23:01,510 [MainThread  ] [INFO ]  PROGRESS: at sentence #1950000, processed 19140379 words, keeping 720121 word types
2017-10-12 18:23:02,983 [MainThread  ] [INFO ]  PROGRESS: at sentence #19600

2017-10-12 18:24:28,792 [MainThread  ] [INFO ]  PROGRESS: at sentence #2520000, processed 24724747 words, keeping 860984 word types
2017-10-12 18:24:30,287 [MainThread  ] [INFO ]  PROGRESS: at sentence #2530000, processed 24818734 words, keeping 863684 word types
2017-10-12 18:24:31,810 [MainThread  ] [INFO ]  PROGRESS: at sentence #2540000, processed 24916278 words, keeping 866397 word types
2017-10-12 18:24:33,293 [MainThread  ] [INFO ]  PROGRESS: at sentence #2550000, processed 25012085 words, keeping 868897 word types
2017-10-12 18:24:34,848 [MainThread  ] [INFO ]  PROGRESS: at sentence #2560000, processed 25110922 words, keeping 871757 word types
2017-10-12 18:24:36,426 [MainThread  ] [INFO ]  PROGRESS: at sentence #2570000, processed 25214223 words, keeping 873900 word types
2017-10-12 18:24:38,005 [MainThread  ] [INFO ]  PROGRESS: at sentence #2580000, processed 25317784 words, keeping 876085 word types
2017-10-12 18:24:39,466 [MainThread  ] [INFO ]  PROGRESS: at sentence #25900

...

2017-10-12 18:30:50,469 [MainThread  ] [INFO ]  PROGRESS: at sentence #5010000, processed 49158722 words, keeping 1407376 word types
2017-10-12 18:30:52,030 [MainThread  ] [INFO ]  PROGRESS: at sentence #5020000, processed 49258227 words, keeping 1409530 word types
2017-10-12 18:30:53,651 [MainThread  ] [INFO ]  PROGRESS: at sentence #5030000, processed 49362018 words, keeping 1411341 word types
2017-10-12 18:30:55,250 [MainThread  ] [INFO ]  PROGRESS: at sentence #5040000, processed 49462797 words, keeping 1413163 word types
2017-10-12 18:30:56,815 [MainThread  ] [INFO ]  PROGRESS: at sentence #5050000, processed 49559361 words, keeping 1415600 word types
2017-10-12 18:30:58,406 [MainThread  ] [INFO ]  PROGRESS: at sentence #5060000, processed 49659389 words, keeping 1417342 word types
2017-10-12 18:30:59,963 [MainThread  ] [INFO ]  PROGRESS: at sentence #5070000, processed 49756573 words, keeping 1418894 word types
2017-10-12 18:31:01,468 [MainThread  ] [INFO ]  PROGRESS: at sentence

2017-10-12 18:32:26,996 [MainThread  ] [INFO ]  PROGRESS: at sentence #5630000, processed 55274884 words, keeping 1524724 word types
2017-10-12 18:32:28,445 [MainThread  ] [INFO ]  PROGRESS: at sentence #5640000, processed 55367187 words, keeping 1526897 word types
2017-10-12 18:32:30,078 [MainThread  ] [INFO ]  PROGRESS: at sentence #5650000, processed 55472402 words, keeping 1528468 word types
2017-10-12 18:32:31,615 [MainThread  ] [INFO ]  PROGRESS: at sentence #5660000, processed 55570643 words, keeping 1530179 word types
2017-10-12 18:32:33,150 [MainThread  ] [INFO ]  PROGRESS: at sentence #5670000, processed 55669940 words, keeping 1531845 word types
2017-10-12 18:32:34,653 [MainThread  ] [INFO ]  PROGRESS: at sentence #5680000, processed 55763731 words, keeping 1533699 word types
2017-10-12 18:32:36,151 [MainThread  ] [INFO ]  PROGRESS: at sentence #5690000, processed 55859055 words, keeping 1535009 word types
2017-10-12 18:32:37,562 [MainThread  ] [INFO ]  PROGRESS: at sentence

2017-10-12 18:34:03,534 [MainThread  ] [INFO ]  PROGRESS: at sentence #6250000, processed 61379366 words, keeping 1639630 word types
2017-10-12 18:34:05,115 [MainThread  ] [INFO ]  PROGRESS: at sentence #6260000, processed 61480374 words, keeping 1641114 word types
2017-10-12 18:34:06,639 [MainThread  ] [INFO ]  PROGRESS: at sentence #6270000, processed 61577322 words, keeping 1642927 word types
2017-10-12 18:34:08,122 [MainThread  ] [INFO ]  PROGRESS: at sentence #6280000, processed 61669865 words, keeping 1644535 word types
2017-10-12 18:34:09,678 [MainThread  ] [INFO ]  PROGRESS: at sentence #6290000, processed 61769049 words, keeping 1646448 word types
2017-10-12 18:34:11,190 [MainThread  ] [INFO ]  PROGRESS: at sentence #6300000, processed 61866214 words, keeping 1648511 word types
2017-10-12 18:34:12,792 [MainThread  ] [INFO ]  PROGRESS: at sentence #6310000, processed 61969439 words, keeping 1650458 word types
2017-10-12 18:34:14,290 [MainThread  ] [INFO ]  PROGRESS: at sentence

2017-10-12 18:35:39,926 [MainThread  ] [INFO ]  PROGRESS: at sentence #6870000, processed 67450635 words, keeping 1753042 word types
2017-10-12 18:35:41,478 [MainThread  ] [INFO ]  PROGRESS: at sentence #6880000, processed 67545656 words, keeping 1755223 word types
2017-10-12 18:35:42,953 [MainThread  ] [INFO ]  PROGRESS: at sentence #6890000, processed 67637120 words, keeping 1756828 word types
2017-10-12 18:35:44,542 [MainThread  ] [INFO ]  PROGRESS: at sentence #6900000, processed 67738331 words, keeping 1758552 word types
2017-10-12 18:35:46,067 [MainThread  ] [INFO ]  PROGRESS: at sentence #6910000, processed 67834194 words, keeping 1760527 word types
2017-10-12 18:35:47,553 [MainThread  ] [INFO ]  PROGRESS: at sentence #6920000, processed 67929054 words, keeping 1762682 word types
2017-10-12 18:35:49,033 [MainThread  ] [INFO ]  PROGRESS: at sentence #6930000, processed 68023584 words, keeping 1764568 word types
2017-10-12 18:35:50,714 [MainThread  ] [INFO ]  PROGRESS: at sentence

2017-10-12 18:37:16,688 [MainThread  ] [INFO ]  PROGRESS: at sentence #7490000, processed 73540012 words, keeping 1861642 word types
2017-10-12 18:37:18,285 [MainThread  ] [INFO ]  PROGRESS: at sentence #7500000, processed 73640190 words, keeping 1863381 word types
2017-10-12 18:37:19,892 [MainThread  ] [INFO ]  PROGRESS: at sentence #7510000, processed 73741437 words, keeping 1864897 word types
2017-10-12 18:37:21,534 [MainThread  ] [INFO ]  PROGRESS: at sentence #7520000, processed 73845281 words, keeping 1866285 word types
2017-10-12 18:37:23,185 [MainThread  ] [INFO ]  PROGRESS: at sentence #7530000, processed 73946314 words, keeping 1867765 word types
2017-10-12 18:37:24,820 [MainThread  ] [INFO ]  PROGRESS: at sentence #7540000, processed 74050611 words, keeping 1869530 word types
2017-10-12 18:37:26,382 [MainThread  ] [INFO ]  PROGRESS: at sentence #7550000, processed 74147311 words, keeping 1871156 word types


In [ ]:
model.save('../data/lingvo/w2v_300_sg_5_w10_trigram')

In [25]:
!ls -sh ../data/lingvo/w2v_300_sg_5_w10_trigram

241M ../data/lingvo/w2v_300_sg_5_w10_trigram


# Doc2Vec

In [ ]:
model = Doc2Vec(Documents(), size=300, window=8, min_count=5, dm=1, workers=cpu_count-1)

2017-10-14 04:11:08,850 [MainThread  ] [INFO ]  collecting all words and their counts
2017-10-14 04:11:08,854 [MainThread  ] [INFO ]  PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2017-10-14 04:11:19,029 [MainThread  ] [INFO ]  PROGRESS: at example #10000, processed 8123140 words (798439/s), 236646 word types, 10000 tags
2017-10-14 04:11:29,318 [MainThread  ] [INFO ]  PROGRESS: at example #20000, processed 16424932 words (807042/s), 394754 word types, 20000 tags
2017-10-14 04:11:39,616 [MainThread  ] [INFO ]  PROGRESS: at example #30000, processed 24640670 words (797992/s), 534330 word types, 30000 tags
2017-10-14 04:11:49,727 [MainThread  ] [INFO ]  PROGRESS: at example #40000, processed 32746968 words (801854/s), 653669 word types, 40000 tags
2017-10-14 04:11:59,823 [MainThread  ] [INFO ]  PROGRESS: at example #50000, processed 40811158 words (798911/s), 763362 word types, 50000 tags
2017-10-14 04:12:09,537 [MainThread  ] [INFO ]  PROGRESS: at example #60000,

2017-10-14 04:28:33,357 [MainThread  ] [INFO ]  PROGRESS: at example #1000000, processed 822139110 words (796578/s), 6568441 word types, 1000000 tags
2017-10-14 04:28:43,898 [MainThread  ] [INFO ]  PROGRESS: at example #1010000, processed 830455121 words (788996/s), 6617694 word types, 1010000 tags
2017-10-14 04:28:54,400 [MainThread  ] [INFO ]  PROGRESS: at example #1020000, processed 838811802 words (795839/s), 6666938 word types, 1020000 tags
2017-10-14 04:29:04,442 [MainThread  ] [INFO ]  PROGRESS: at example #1030000, processed 846868001 words (802325/s), 6714353 word types, 1030000 tags
2017-10-14 04:29:14,646 [MainThread  ] [INFO ]  PROGRESS: at example #1040000, processed 855081541 words (805088/s), 6761334 word types, 1040000 tags
2017-10-14 04:29:24,810 [MainThread  ] [INFO ]  PROGRESS: at example #1050000, processed 863168364 words (795767/s), 6803477 word types, 1050000 tags
2017-10-14 04:29:35,227 [MainThread  ] [INFO ]  PROGRESS: at example #1060000, processed 871346969 w

2017-10-14 04:34:42,886 [MainThread  ] [INFO ]  PROGRESS: at 0.24% examples, 338659 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:43,976 [MainThread  ] [INFO ]  PROGRESS: at 0.25% examples, 338365 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:34:44,993 [MainThread  ] [INFO ]  PROGRESS: at 0.25% examples, 338995 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:46,021 [MainThread  ] [INFO ]  PROGRESS: at 0.26% examples, 339281 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:47,024 [MainThread  ] [INFO ]  PROGRESS: at 0.27% examples, 339326 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:48,032 [MainThread  ] [INFO ]  PROGRESS: at 0.27% examples, 339289 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:49,072 [MainThread  ] [INFO ]  PROGRESS: at 0.28% examples, 339036 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:34:50,073 [MainThread  ] [INFO ]  PROGRESS: at 0.29% examples, 339677 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:34:51,081 [MainThread  ] [INFO ]  PROGRESS: at 0.3

2017-10-14 04:35:55,354 [MainThread  ] [INFO ]  PROGRESS: at 0.76% examples, 341927 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:56,357 [MainThread  ] [INFO ]  PROGRESS: at 0.77% examples, 342049 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:57,365 [MainThread  ] [INFO ]  PROGRESS: at 0.78% examples, 341993 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:58,374 [MainThread  ] [INFO ]  PROGRESS: at 0.79% examples, 342004 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:35:59,433 [MainThread  ] [INFO ]  PROGRESS: at 0.79% examples, 341791 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:00,437 [MainThread  ] [INFO ]  PROGRESS: at 0.80% examples, 341914 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:01,445 [MainThread  ] [INFO ]  PROGRESS: at 0.81% examples, 341858 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:02,449 [MainThread  ] [INFO ]  PROGRESS: at 0.81% examples, 342030 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:36:03,454 [MainThread  ] [INFO ]  PROGRESS: at 0.8

2017-10-14 04:37:07,727 [MainThread  ] [INFO ]  PROGRESS: at 1.30% examples, 343877 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:08,739 [MainThread  ] [INFO ]  PROGRESS: at 1.30% examples, 343882 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:09,752 [MainThread  ] [INFO ]  PROGRESS: at 1.31% examples, 344014 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:10,778 [MainThread  ] [INFO ]  PROGRESS: at 1.32% examples, 344198 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:11,790 [MainThread  ] [INFO ]  PROGRESS: at 1.33% examples, 344375 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:37:12,794 [MainThread  ] [INFO ]  PROGRESS: at 1.33% examples, 344473 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:13,877 [MainThread  ] [INFO ]  PROGRESS: at 1.34% examples, 344486 words/s, in_qsize 0, out_qsize 1
2017-10-14 04:37:14,912 [MainThread  ] [INFO ]  PROGRESS: at 1.35% examples, 344550 words/s, in_qsize 0, out_qsize 0
2017-10-14 04:37:15,959 [MainThread  ] [INFO ]  PROGRESS: at 1.3

...

2017-10-14 05:40:28,222 [MainThread  ] [INFO ]  PROGRESS: at 29.13% examples, 349797 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:29,229 [MainThread  ] [INFO ]  PROGRESS: at 29.14% examples, 349798 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:30,231 [MainThread  ] [INFO ]  PROGRESS: at 29.14% examples, 349797 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:31,258 [MainThread  ] [INFO ]  PROGRESS: at 29.15% examples, 349793 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:32,282 [MainThread  ] [INFO ]  PROGRESS: at 29.16% examples, 349789 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:33,336 [MainThread  ] [INFO ]  PROGRESS: at 29.17% examples, 349787 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:34,349 [MainThread  ] [INFO ]  PROGRESS: at 29.17% examples, 349791 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:35,380 [MainThread  ] [INFO ]  PROGRESS: at 29.18% examples, 349793 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:40:36,399 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:41:39,484 [MainThread  ] [INFO ]  PROGRESS: at 29.65% examples, 349849 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:40,502 [MainThread  ] [INFO ]  PROGRESS: at 29.66% examples, 349851 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:41,542 [MainThread  ] [INFO ]  PROGRESS: at 29.66% examples, 349853 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:42,558 [MainThread  ] [INFO ]  PROGRESS: at 29.67% examples, 349854 words/s, in_qsize 0, out_qsize 1
2017-10-14 05:41:43,586 [MainThread  ] [INFO ]  PROGRESS: at 29.68% examples, 349857 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:44,601 [MainThread  ] [INFO ]  PROGRESS: at 29.69% examples, 349856 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:45,618 [MainThread  ] [INFO ]  PROGRESS: at 29.69% examples, 349857 words/s, in_qsize 1, out_qsize 0
2017-10-14 05:41:46,649 [MainThread  ] [INFO ]  PROGRESS: at 29.70% examples, 349855 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:41:47,699 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:42:50,656 [MainThread  ] [INFO ]  PROGRESS: at 30.18% examples, 349910 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:51,668 [MainThread  ] [INFO ]  PROGRESS: at 30.18% examples, 349909 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:52,671 [MainThread  ] [INFO ]  PROGRESS: at 30.19% examples, 349911 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:53,689 [MainThread  ] [INFO ]  PROGRESS: at 30.20% examples, 349908 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:54,704 [MainThread  ] [INFO ]  PROGRESS: at 30.20% examples, 349905 words/s, in_qsize 0, out_qsize 1
2017-10-14 05:42:55,737 [MainThread  ] [INFO ]  PROGRESS: at 30.21% examples, 349910 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:56,738 [MainThread  ] [INFO ]  PROGRESS: at 30.22% examples, 349908 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:57,788 [MainThread  ] [INFO ]  PROGRESS: at 30.23% examples, 349907 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:42:58,795 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:44:02,099 [MainThread  ] [INFO ]  PROGRESS: at 30.70% examples, 349915 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:03,113 [MainThread  ] [INFO ]  PROGRESS: at 30.71% examples, 349916 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:04,142 [MainThread  ] [INFO ]  PROGRESS: at 30.71% examples, 349916 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:05,154 [MainThread  ] [INFO ]  PROGRESS: at 30.72% examples, 349921 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:06,213 [MainThread  ] [INFO ]  PROGRESS: at 30.73% examples, 349916 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:07,225 [MainThread  ] [INFO ]  PROGRESS: at 30.74% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:08,235 [MainThread  ] [INFO ]  PROGRESS: at 30.74% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:09,241 [MainThread  ] [INFO ]  PROGRESS: at 30.75% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:44:10,242 [MainThread  ] [INFO ]  PROGRESS

2017-10-14 05:45:13,516 [MainThread  ] [INFO ]  PROGRESS: at 31.22% examples, 349920 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:14,538 [MainThread  ] [INFO ]  PROGRESS: at 31.22% examples, 349918 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:15,565 [MainThread  ] [INFO ]  PROGRESS: at 31.23% examples, 349922 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:16,576 [MainThread  ] [INFO ]  PROGRESS: at 31.24% examples, 349921 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:17,596 [MainThread  ] [INFO ]  PROGRESS: at 31.25% examples, 349923 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:18,628 [MainThread  ] [INFO ]  PROGRESS: at 31.25% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:19,637 [MainThread  ] [INFO ]  PROGRESS: at 31.26% examples, 349924 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:20,646 [MainThread  ] [INFO ]  PROGRESS: at 31.27% examples, 349923 words/s, in_qsize 0, out_qsize 0
2017-10-14 05:45:21,650 [MainThread  ] [INFO ]  PROGRESS

In [ ]:
model.save('../data/lingvo/d2v_s300_w8_mc5_dm1_iter5')

# Save for Misha

In [4]:
trigram_ph = gensim.models.phrases.Phraser.load('../data/lingvo/trigram_ph')

2017-10-12 18:05:09,826 [MainThread  ] [INFO ]  loading Phraser object from ../data/lingvo/trigram_ph
2017-10-12 18:05:11,761 [MainThread  ] [INFO ]  loaded ../data/lingvo/trigram_ph


In [1]:
c = 0
l = []
for k,v in tqdm_notebook(trigram_ph.phrasegrams.items()):
    if v[0] > 7 and v[1] > 100:
        the_string = '_'.join(k)
        if re.search('[а-яА-Яa-zA-Z]', k[0]) and re.search('[а-яА-Яa-zA-Z]', k[1]):
            c+=1
            l.append([the_string, v[0], v[1]])
#         print('%s_%s %s' % (k[0], k[1], v))
        
df = pd.DataFrame(l)

NameError: name 'tqdm_notebook' is not defined

In [ ]:
# df.sort_values(by=1, ascending=False)

In [13]:
len(df[0].unique())

946933

In [14]:
with GzipFile('../data/collocations_trigram.txt.gz', 'w') as f:
    for tag in sorted(df[0].unique()):
        f.write(tag + '\n')

In [2]:
import xml.etree.ElementTree as ET

tree = ET.parse('../data/TestDocumentsResult.xml')
root = tree.getroot()

In [30]:
gold = {}
for child in root:
    sims = []
    for similars in child:
        for sim in similars:
            sims.append(sim.attrib['docId'])
    gold[child.attrib['docId']] = sims